<a href="https://colab.research.google.com/github/Ayanlola2002/kaggle_challenge/blob/master/Tunde_competition.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install kaggle
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/

    100% |████████████████████████████████| 61kB 2.5MB/s 
    100% |████████████████████████████████| 245kB 7.5MB/s 
  Running setup.py bdist_wheel for kaggle ... - \ done
  Stored in directory: /root/.cache/pip/wheels/8b/21/3b/a0076243c6ae12a6215b2da515fe06b539aee7217b406e510e
  Running setup.py bdist_wheel for python-slugify ... - done
  Stored in directory: /root/.cache/pip/wheels/e3/65/da/2045deea3098ed7471eca0e2460cfbd3fdfe8c1d6fa6fcac92
Successfully built kaggle python-slugify


In [2]:
!kaggle --version

Kaggle API 1.5.0


In [3]:
!kaggle competitions download -c hackexpo2018-pre-competition

  0% 0.00/430k [00:00<?, ?B/s]
100% 430k/430k [00:00<00:00, 74.8MB/s]
 56% 5.00M/8.93M [00:00<00:00, 35.2MB/s]
100% 8.93M/8.93M [00:00<00:00, 57.5MB/s]
 76% 41.0M/53.9M [00:00<00:00, 66.2MB/s]
100% 53.9M/53.9M [00:00<00:00, 115MB/s] 


In [0]:
import glob as glob
import numpy as np
from PIL import Image
from sklearn.utils import shuffle
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
import os
import tensorflow as tf

In [0]:
def prepare_test_data(dir):
    os.chdir(dir)
    imgarr=[]
    imgid=glob.glob('*')
    for i in imgid:
        imgarr.append(np.asarray(Image.open(i).convert('L')).flatten())
        pass
    imgarr=np.array(imgarr)/255
    os.chdir('../')
    return [imgarr,imgid]

In [0]:
def prepare_train_data(dir):
    folders=glob.glob(dir+'*')
    img_dir=[]
    labels=[]
    imgarr=[]
    for i in folders:
        img_dir+=glob.glob(i+'/*')
        labels+=[int(i[-1])]*len(glob.glob(i+'/*'))
        pass
    
    for i in img_dir:
        imgarr.append(np.asarray(Image.open(i).convert('L')).flatten())
        pass
    
    imgarr=np.array(imgarr)/255
    
    labels=np.reshape(np.array(labels,dtype=np.float),(len(labels),1))
    
    ohe=OneHotEncoder(sparse=False)
    
    labels=ohe.fit_transform(labels)
    
    data,label=shuffle(imgarr,labels,random_state=1234)
    
    #np.save('tarin_data.npy',traindata)
    
    return data,label
    

In [7]:
!unzip train
!unzip test

Archive:  train.zip
   creating: train/
   creating: train/0/
  inflating: train/0/00035d84-796a-4d57-afb9-f38fcf72695d.jpg  
  inflating: train/0/0009937d-8e82-4671-8dfa-8afbdd962493.jpg  
  inflating: train/0/000a3e1c-461e-495c-bcbb-2f6a141ad1f3.jpg  
  inflating: train/0/001a059e-b1d7-417c-9de2-1a2d9997d2cb.jpg  
  inflating: train/0/001be145-4d60-4ad9-82cf-5e3ffdff122c.jpg  
  inflating: train/0/0031f4e0-dcef-4133-b3cd-550ed34c67e4.jpg  
  inflating: train/0/0061cdfc-98d6-40a0-a2f8-01fc71eacb52.jpg  
  inflating: train/0/00630f4e-26ea-453b-b0f0-51ffd9c302e1.jpg  
  inflating: train/0/00719d9f-3953-4701-ad2a-6c3f4d7362ad.jpg  
  inflating: train/0/0072a637-dbdb-4f2b-a6f4-fd4e19695eac.jpg  
  inflating: train/0/007834e2-3959-4577-bbf1-f0b1b796e4aa.jpg  
  inflating: train/0/009c65f5-67b3-42ba-9561-bdc1cb522697.jpg  
  inflating: train/0/00bc150f-4ca7-4eca-a65f-9b2f759afbf9.jpg  
  inflating: train/0/00bf5488-5917-4769-942a-78e438ea027e.jpg  
  inflating: train/0/00c6a24e-e11b-4853-a2

In [0]:
data,label=prepare_train_data('train/')

In [9]:
from __future__ import print_function
import keras
from sklearn.model_selection import train_test_split
from keras.datasets import mnist
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten
from keras.layers import Conv2D, MaxPooling2D
from keras import backend as K

batch_size = 128
num_classes = 10
epochs = 12

# input image dimensions
img_rows, img_cols = 28, 28

# the data, split between train and test sets
x_train, x_test, y_train, y_test = train_test_split(data,label,test_size=0.3,random_state=12345)

if K.image_data_format() == 'channels_first':
    x_train = x_train.reshape(x_train.shape[0], 1, img_rows, img_cols)
    x_test = x_test.reshape(x_test.shape[0], 1, img_rows, img_cols)
    input_shape = (1, img_rows, img_cols)
else:
    x_train = x_train.reshape(x_train.shape[0], img_rows, img_cols, 1)
    x_test = x_test.reshape(x_test.shape[0], img_rows, img_cols, 1)
    input_shape = (img_rows, img_cols, 1)

x_train = x_train.astype('float32')
x_test = x_test.astype('float32')

print('x_train shape:', x_train.shape)
print(x_train.shape[0], 'train samples')
print(x_test.shape[0], 'test samples')

# convert class vectors to binary class matrices
# y_train = keras.utils.to_categorical(y_train, num_classes)
# y_test = keras.utils.to_categorical(y_test, num_classes)

model = Sequential()
model.add(Conv2D(32, kernel_size=(3, 3),
                 activation='relu',
                 input_shape=input_shape))
model.add(Conv2D(64, (3, 3), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.25))
model.add(Flatten())
model.add(Dense(128, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(num_classes, activation='softmax'))

model.compile(loss=keras.losses.categorical_crossentropy,
              optimizer=keras.optimizers.Adadelta(),
              metrics=['accuracy'])

model.fit(x_train, y_train,
          batch_size=batch_size,
          epochs=epochs,
          verbose=1,
          validation_data=(x_test, y_test))
score = model.evaluate(x_test, y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])

Using TensorFlow backend.


x_train shape: (42000, 28, 28, 1)
42000 train samples
18000 test samples
Train on 42000 samples, validate on 18000 samples
Epoch 1/12
42000/42000 [==============================] - 126s 3ms/step - loss: 0.6239 - acc: 0.7786 - val_loss: 0.4398 - val_acc: 0.8297
Epoch 2/12
42000/42000 [==============================] - 123s 3ms/step - loss: 0.3931 - acc: 0.8615 - val_loss: 0.3902 - val_acc: 0.8559
Epoch 3/12
42000/42000 [==============================] - 124s 3ms/step - loss: 0.3419 - acc: 0.8789 - val_loss: 0.3264 - val_acc: 0.8821
Epoch 4/12
42000/42000 [==============================] - 124s 3ms/step - loss: 0.3119 - acc: 0.8874 - val_loss: 0.2819 - val_acc: 0.9008
Epoch 5/12
42000/42000 [==============================] - 125s 3ms/step - loss: 0.2877 - acc: 0.8966 - val_loss: 0.2761 - val_acc: 0.8972
Epoch 6/12
42000/42000 [==============================] - 125s 3ms/step - loss: 0.2674 - acc: 0.9038 - val_loss: 0.2570 - val_acc: 0.9067
Epoch 7/12
42000/42000 [=========================

In [0]:
test_data=prepare_test_data('test/')

In [0]:
test_data=prepare_test_data('test/')

In [0]:
predictions=model.predict(np.reshape(test_data[0],(-1,28,28,1)))


In [0]:
answer=[]
for i in predictions:
  i=np.argmax(i,axis=0)
  answer.append(i)

In [0]:
import pandas as pd
submission=pd.DataFrame({'ImageID':test_data[1],'Category':answer})

In [0]:
submission.to_csv('tunde.csv',index=False)

In [17]:
!kaggle competitions submit -c hackexpo2018-pre-competition -f tunde.csv -m "Hack"


100% 420k/420k [00:02<00:00, 190kB/s]
Successfully submitted to HackExpo2018 Pre-Competition

In [19]:
!kaggle competitions leaderboard -s hackexpo2018-pre-competition

 teamId  teamName            submissionDate       score    
-------  ------------------  -------------------  -------  
2400257  Deven               2018-11-22 03:50:58  0.93400  
2400622  Akinde Abdullah     2018-11-21 23:02:46  0.93050  
2385310  Izuchukwu           2018-11-21 12:43:49  0.92975  
2384597  hamzat ibrahim      2018-11-21 14:36:22  0.92950  
2385186  rahman              2018-11-21 17:04:36  0.92425  
2369292  Tej                 2018-11-21 09:41:19  0.92400  
2401674  Al-ameen            2018-11-21 17:01:00  0.92375  
2381833  Evbodaghe David     2018-11-20 21:37:09  0.92350  
2418208  John                2018-11-21 17:00:49  0.92300  
2411905  Ewomazino           2018-11-21 19:02:30  0.92200  
2399802  Eyitayo Ogunbiyi    2018-11-21 13:20:25  0.92125  
2381207  Abayorme            2018-11-21 22:39:15  0.91950  
2383737  Rising Odegua       2018-11-21 10:45:55  0.91775  
2381140  sadiq ade           2018-11-21 19:09:52  0.91775  
2406595  Aanu Babajide       2018-11-19 